<a href="https://colab.research.google.com/github/akkumaha/aws-tutorial-code/blob/master/CNN.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
# Load the Drive helper and mount
from google.colab import drive
drive.mount('/content/drive')

MessageError: ignored

In [14]:
pip install torch torchvision tqdm

In [3]:
pip install Pillow

In [4]:
#(a)
import numpy as np
import pickle
import os
import torch
import torchvision.transforms as transforms
from torch.utils.data import DataLoader, Dataset
from PIL import Image

# Define a PyTorch Dataset class to handle the CIFAR-10 data
class CIFAR10Dataset(Dataset):
    def __init__(self, file_list, meta_file, transform=None):
        self.transform = transform
        self.data = []
        self.labels = []

        # Load class names from the meta file
        with open(meta_file, 'rb') as infile:
            data_dict = pickle.load(infile, encoding='bytes')
            self.class_names = data_dict[b'label_names']

        # Load data from files
        for file_name in file_list:
            with open(file_name, 'rb') as infile:
                data_dict = pickle.load(infile, encoding='bytes')
                self.data.append(data_dict[b'data'])
                self.labels.extend(data_dict[b'labels'])

        self.data = np.vstack(self.data).reshape(-1, 3, 32, 32)
        self.data = self.data.transpose((0, 2, 3, 1))  # Convert to HWC format

    def __len__(self):
        return len(self.data)

    def __getitem__(self, index):
        img, label = self.data[index], self.labels[index]
        img = Image.fromarray(img)

        if self.transform:
            img = self.transform(img)

        return img, label

# Define the transform for data augmentation for the training data
train_transform = transforms.Compose([
    transforms.Resize(36),  # Resize to 36x36
    transforms.RandomCrop(32, padding=5),  # Random crop with 5 pixels of padding
    transforms.RandomHorizontalFlip(),  # Horizontal flip
    transforms.RandomRotation(20),  # Rotation by +/- 20 degrees
    transforms.RandomResizedCrop(32, scale=(0.6, 1.0)),  # Scaling and cropping back to 32x32
    transforms.ToTensor(),  # Convert images to PyTorch tensors
    transforms.Normalize((0.5, 0.5, 0.5), (0.5, 0.5, 0.5))  # Normalize the images
])
print("Train_Transform")

# No augmentation for the test set
test_transform = transforms.Compose([
    transforms.Resize(32),  # Resize to 32x32 to match the input size of the network
    transforms.ToTensor(),  # Convert images to PyTorch tensors
    transforms.Normalize((0.5, 0.5, 0.5), (0.5, 0.5, 0.5))  # Normalize the images
])
print("Test_Transform")

# Define file paths
data_path = '/content/drive/My Drive/cifar-10-batches-py'
train_files = [os.path.join(data_path, 'data_batch_{}'.format(i)) for i in range(1, 6)]
test_files = [os.path.join(data_path, 'test_batch')]
meta_file = os.path.join(data_path, 'batches.meta')

# Create datasets
train_dataset = CIFAR10Dataset(train_files, meta_file, transform=train_transform)
test_dataset = CIFAR10Dataset(test_files, meta_file, transform=test_transform)
print("Created Datasets")

# Create dataloaders
train_loader = DataLoader(train_dataset, batch_size=64, shuffle=True, num_workers=2)
test_loader = DataLoader(test_dataset, batch_size=64, shuffle=False, num_workers=2)
print("Created Dataloaders")

Train_Transform
Test_Transform
Created Datasets
Created Dataloaders


In [5]:
#(b)
import torch
import torch.nn as nn
import torch.nn.functional as F

class BaseNet(nn.Module):
    def __init__(self, num_blocks):
        super(BaseNet, self).__init__()
        self.num_blocks = num_blocks

        # Initial Convolution layer
        self.init_conv = nn.Conv2d(3, 16, kernel_size=3, stride=1, padding=1)
        self.init_bn = nn.BatchNorm2d(16)
        self.init_relu = nn.ReLU(inplace=True)

        # Modules
        self.module1 = self._make_module(16, 16, num_blocks, stride=1)
        self.module2 = self._make_module(16, 32, num_blocks, stride=2)
        self.module3 = self._make_module(32, 64, num_blocks, stride=2)

        # Global Average Pooling
        self.global_avg_pool = nn.AdaptiveAvgPool2d((1, 1))

        # Fully Connected Layer
        self.fc = nn.Linear(64, 10)

    def _make_module(self, in_channels, out_channels, num_blocks, stride):
        layers = []

        # First layer of the module with stride 2 for downsampling
        layers.append(nn.Sequential(
            nn.Conv2d(in_channels, out_channels, kernel_size=3, stride=stride, padding=1),
            nn.BatchNorm2d(out_channels),
            nn.ReLU(inplace=True)
        ))

        # Remaining layers of the module with stride 1
        for _ in range(1, num_blocks):
            layers.append(nn.Sequential(
                nn.Conv2d(out_channels, out_channels, kernel_size=3, stride=1, padding=1),
                nn.BatchNorm2d(out_channels),
                nn.ReLU(inplace=True)
            ))

        return nn.Sequential(*layers)

    def forward(self, x):
        x = self.init_conv(x)
        x = self.init_bn(x)
        x = self.init_relu(x)

        x = self.module1(x)
        x = self.module2(x)
        x = self.module3(x)

        x = self.global_avg_pool(x)
        x = torch.flatten(x, 1)
        x = self.fc(x)

        return x

# Define the number of blocks for BaseNet-20 and BaseNet-32
num_blocks_20 = 6  # 6 blocks in each module for BaseNet-20
num_blocks_32 = 10  # 10 blocks in each module for BaseNet-32

# Create instances of BaseNet-20 and BaseNet-32
base_net_20 = BaseNet(num_blocks=num_blocks_20)
base_net_32 = BaseNet(num_blocks=num_blocks_32)

print(base_net_20)
print(base_net_32)


BaseNet(
  (init_conv): Conv2d(3, 16, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
  (init_bn): BatchNorm2d(16, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (init_relu): ReLU(inplace=True)
  (module1): Sequential(
    (0): Sequential(
      (0): Conv2d(16, 16, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
      (1): BatchNorm2d(16, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (2): ReLU(inplace=True)
    )
    (1): Sequential(
      (0): Conv2d(16, 16, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
      (1): BatchNorm2d(16, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (2): ReLU(inplace=True)
    )
    (2): Sequential(
      (0): Conv2d(16, 16, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1))
      (1): BatchNorm2d(16, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (2): ReLU(inplace=True)
    )
    (3): Sequential(
      (0): Conv2d(16, 16, kernel_size=(3, 3), stride=(1, 1), pa

In [16]:
#(c)
import torch
import torch.nn as nn
import torch.nn.functional as F

class ResidualBlock(nn.Module):
    """
    A residual block that you can use to build ResNet.
    """
    def __init__(self, in_channels, out_channels, stride=1, downsample=None):
        super(ResidualBlock, self).__init__()
        # First convolutional layer
        self.conv1 = nn.Conv2d(in_channels, out_channels, kernel_size=3, padding=1, stride=stride, bias=False)
        self.bn1 = nn.BatchNorm2d(out_channels)
        # Second convolutional layer
        self.conv2 = nn.Conv2d(out_channels, out_channels, kernel_size=3, padding=1, bias=False)
        self.bn2 = nn.BatchNorm2d(out_channels)
        # The downsample layer will adjust the dimensions of the residual (identity) path if necessary
        self.downsample = downsample

    def forward(self, x):
        # Store the original x for the residual connection
        residual = x

        # Pass input through conv1 -> bn1 -> ReLU
        out = self.conv1(x)
        out = self.bn1(out)
        out = F.relu(out)

        # Pass input through conv2 -> bn2
        out = self.conv2(out)
        out = self.bn2(out)

        # If a downsample exists, apply it to the residual
        if self.downsample:
            residual = self.downsample(x)

        # Add the residual to the output of the convolutional layers
        out += residual
        out = F.relu(out)  # Apply ReLU after adding the residual
        return out

class ResNet(nn.Module):
    """
    A ResNet model that uses the above ResidualBlock.
    """
    def __init__(self, block, num_blocks, num_classes=10):
        super(ResNet, self).__init__()
        self.in_channels = 16

        # Initial convolutional layer
        self.conv1 = nn.Conv2d(3, 16, kernel_size=3, stride=1, padding=1, bias=False)
        self.bn1 = nn.BatchNorm2d(16)

        # Create the ResNet layers
        self.layer1 = self.make_resnet_layer(block, 16, num_blocks[0], stride=1)
        self.layer2 = self.make_resnet_layer(block, 32, num_blocks[1], stride=2)
        self.layer3 = self.make_resnet_layer(block, 64, num_blocks[2], stride=2)

        # Global average pooling followed by a fully connected layer
        self.global_avg_pool = nn.AdaptiveAvgPool2d((1, 1))
        self.fc = nn.Linear(64, num_classes)

    def make_resnet_layer(self, block, out_channels, num_blocks, stride):
        # This function creates a single layer of residual blocks
        downsample = None
        if stride != 1 or self.in_channels != out_channels:
            downsample = nn.Sequential(
                nn.Conv2d(self.in_channels, out_channels, kernel_size=1, stride=stride, bias=False),
                nn.BatchNorm2d(out_channels))

        layers = []
        layers.append(block(self.in_channels, out_channels, stride, downsample))
        self.in_channels = out_channels
        for _ in range(1, num_blocks):
            layers.append(block(out_channels, out_channels))

        return nn.Sequential(*layers)

    def forward(self, x):
        # Forward pass through the initial conv layer and then the layers of residual blocks
        out = F.relu(self.bn1(self.conv1(x)))
        out = self.layer1(out)
        out = self.layer2(out)
        out = self.layer3(out)

        # Apply global average pooling and pass through the fully connected layer
        out = self.global_avg_pool(out)
        out = out.view(out.size(0), -1)  # Flatten the tensor for the fully connected layer
        out = self.fc(out)
        return out

def ResNet20():
    # 3 modules, each with 3 blocks, for ResNet-20
    return ResNet(ResidualBlock, [3, 3, 3], num_classes=10)

def ResNet32():
    # 3 modules, each with 5 blocks, for ResNet-32
    return ResNet(ResidualBlock, [5, 5, 5], num_classes=10)


# Create model instances
resnet20 = ResNet20()
resnet32 = ResNet32()

print(resnet20)
print(resnet32)


ResNet(
  (conv1): Conv2d(3, 16, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
  (bn1): BatchNorm2d(16, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
  (layer1): Sequential(
    (0): ResidualBlock(
      (conv1): Conv2d(16, 16, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
      (bn1): BatchNorm2d(16, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (conv2): Conv2d(16, 16, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
      (bn2): BatchNorm2d(16, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
    )
    (1): ResidualBlock(
      (conv1): Conv2d(16, 16, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
      (bn1): BatchNorm2d(16, eps=1e-05, momentum=0.1, affine=True, track_running_stats=True)
      (conv2): Conv2d(16, 16, kernel_size=(3, 3), stride=(1, 1), padding=(1, 1), bias=False)
      (bn2): BatchNorm2d(16, eps=1e-05, momentum=0.1, affine=True, track_running_stats

In [17]:
# Cell 1: Imports and Model Definitions

import torch
import torch.nn as nn
import torch.nn.functional as F
import torch.optim as optim
from torch.utils.data import DataLoader
import torchvision
import torchvision.transforms as transforms
from torchvision.datasets import CIFAR10
import numpy as np
import matplotlib.pyplot as plt
from tqdm.notebook import tqdm

# Define BaseNet and ResNet classes here (from previous explanations)
# ...


In [18]:
#Experiments :

In [19]:
#(a)

In [20]:
# Cell 3: Training Function

def train_model(model, train_loader, test_loader, epochs, learning_rate):
    criterion = nn.CrossEntropyLoss()
    optimizer = optim.SGD(model.parameters(), lr=learning_rate, momentum=0.9)
    scheduler = optim.lr_scheduler.StepLR(optimizer, step_size=200, gamma=0.1)

    # Data structures for storing training progress
    train_acc_history, test_acc_history = [], []
    train_loss_history, test_loss_history = [], []

    # Training loop
    for epoch in tqdm(range(epochs), desc='Epochs'):
        model.train()
        running_loss = 0.0
        correct = 0
        total = 0

        # Train over all training data
        for i, (inputs, labels) in enumerate(tqdm(train_loader, desc='Training Batch', leave=False)):
            inputs, labels = inputs.to(device), labels.to(device)
            optimizer.zero_grad()

            # Forward + backward + optimize
            outputs = model(inputs)
            loss = criterion(outputs, labels)
            loss.backward()
            optimizer.step()

            running_loss += loss.item()
            _, predicted = outputs.max(1)
            total += labels.size(0)
            correct += predicted.eq(labels).sum().item()

        train_loss = running_loss / len(train_loader)
        train_acc = 100.*correct/total
        train_loss_history.append(train_loss)
        train_acc_history.append(train_acc)

        # Evaluate on test data
        model.eval()
        test_loss = 0.0
        correct = 0
        total = 0
        with torch.no_grad():
            for i, (inputs, labels) in enumerate(tqdm(test_loader, desc='Test Batch', leave=False)):
                inputs, labels = inputs.to(device), labels.to(device)

                outputs = model(inputs)
                loss = criterion(outputs, labels)
                test_loss += loss.item()
                _, predicted = outputs.max(1)
                total += labels.size(0)
                correct += predicted.eq(labels).sum().item()

        test_loss = test_loss / len(test_loader)
        test_acc = 100.*correct/total
        test_loss_history.append(test_loss)
        test_acc_history.append(test_acc)

        scheduler.step()

        print(f'Epoch {epoch+1}: Train Loss: {train_loss:.4f}, Train Accuracy: {train_acc:.2f}, Test Loss: {test_loss:.4f}, Test Accuracy: {test_acc:.2f}')

    return train_loss_history, train_acc_history, test_loss_history, test_acc_history


In [21]:
# Cell 4: Set Device for Training

device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")
print(f'Training on {device}')


Training on cuda:0


In [23]:
# Cell 5: Instantiate and Train Models

# Create instances of BaseNet-20 and BaseNet-32
base_net_20 = BaseNet(num_blocks=6).to(device)
base_net_32 = BaseNet(num_blocks=10).to(device)

# Train BaseNet-20
print("Training BaseNet-20")
bn20_train_loss, bn20_train_acc, bn20_test_loss, bn20_test_acc = train_model(base_net_20, train_loader, test_loader, epochs=50, learning_rate=0.1)

# Train BaseNet-32
print("Training BaseNet-32")
bn32_train_loss, bn32_train_acc, bn32_test_loss, bn32_test_acc = train_model(base_net_32, train_loader, test_loader, epochs=50, learning_rate=0.1)

# Create instances of ResNet-20 and ResNet-32
resnet_20 = ResNet20().to(device)
resnet_32 = ResNet32().to(device)

# Train ResNet-20
print("Training ResNet-20")
rn20_train_loss, rn20_train_acc, rn20_test_loss, rn20_test_acc = train_model(resnet_20, train_loader, test_loader, epochs=50, learning_rate=0.1)

# Train ResNet-32
print("Training ResNet-32")
rn32_train_loss, rn32_train_acc, rn32_test_loss, rn32_test_acc = train_model(resnet_32, train_loader, test_loader, epochs=50, learning_rate=0.1)


Training BaseNet-20


Epochs:   0%|          | 0/50 [00:00<?, ?it/s]

Training Batch:   0%|          | 0/782 [00:00<?, ?it/s]

Test Batch:   0%|          | 0/157 [00:00<?, ?it/s]

Epoch 1: Train Loss: 1.9521, Train Accuracy: 25.70, Test Loss: 1.8552, Test Accuracy: 32.98


...

Test Batch:   0%|          | 0/157 [00:00<?, ?it/s]

Epoch 49: Train Loss: 0.4786, Train Accuracy: 83.32, Test Loss: 0.5867, Test Accuracy: 81.68


Training Batch:   0%|          | 0/782 [00:00<?, ?it/s]

Test Batch:   0%|          | 0/157 [00:00<?, ?it/s]

Epoch 50: Train Loss: 0.4720, Train Accuracy: 83.61, Test Loss: 0.5975, Test Accuracy: 81.68
